In [425]:
# import packages

import pandas_datareader.data as web
import datetime
import pandas as pd
import numpy as np
import scipy.stats as stat
import dateutil.relativedelta
import sys

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.layouts import column
from bokeh.models import Legend
from __future__ import division

import dash
import dash_core_components as dcc
import dash_html_components as html

In [426]:
# Price plot

def plot_price(price, length):
    data = price[:length]
    output_notebook()    
    plot = figure(width=600, height=400, title = "Historical Prices", x_axis_type="datetime")
    plot.line(data.index, data)
    plot.title.text_font_size = '11pt'
    show(plot)

In [427]:

# Calculate estimated parameters for GBM based on x year (in days) rolling windows

def gbm_est(prices, window_days):
    rtn = -np.diff(np.log(prices))
    rtnsq = rtn * rtn
    mubar = list(reversed(np.convolve(rtn, np.ones((window_days,))/window_days, mode='valid')))
    x2bar = list(reversed(np.convolve(rtnsq, np.ones((window_days,))/window_days, mode='valid')))
    var = x2bar - np.square(mubar)
    sigmabar = np.sqrt(np.maximum(var, np.zeros(len(var))))
    sigma = sigmabar / np.sqrt(1/252)
    mu = np.array(mubar)*252 + np.square(sigma)/2
    return rtn, mu, sigma, np.array(mubar), sigmabar

In [428]:
# Parameters plot

def plot_parameters(price):
    rtn_2, mu_2, sigma_2, mubar_2, sigmabar_2 = gbm_est(price, 2*252)
    rtn_5, mu_5, sigma_5, mubar_5, sigmabar_5 = gbm_est(price, 5*252)
    rtn_10, mu_10, sigma_10, mubar_10, sigmabar_10 = gbm_est(price, 10*252)
    length = min(len(mu_2), len(mu_5), len(mu_10), len(sigma_2), len(sigma_5), len(sigma_10))
    mu = pd.DataFrame({'Mu_2': mu_2[:length], 'Mu_5': mu_5[:length], 'Mu_10': mu_10[:length]}, 
                      index = price.index[:length])
    sigma = pd.DataFrame({'Sigma_2': sigma_2[:length], 'Sigma_5': sigma_5[:length], 'Sigma_10': sigma_10[:length]}, 
                         index = price.index[:length])
    output_notebook()    
    pmu = figure(width=600, height=400, title = "Parameter - Mu", x_axis_type="datetime")
    pmu.line(mu.index, mu['Mu_2'], legend = '2-year roling window')
    pmu.line(mu.index, mu['Mu_5'], color = 'green', legend = '5-year roling window')
    pmu.line(mu.index, mu['Mu_10'], color = 'orange', legend = '10-year roling window')
    pmu.title.text_font_size = '11pt'
    pmu.legend.location = 'bottom_right'
    pmu.legend.background_fill_alpha = 0.5
    psigma = figure(width=600, height=400, title = "Parameter - Sigma", x_axis_type="datetime")
    psigma.line(mu.index, sigma['Sigma_2'], legend = '2-year roling window')
    psigma.line(mu.index, sigma['Sigma_5'], color = 'green', legend = '5-year roling window')
    psigma.line(mu.index, sigma['Sigma_10'], color = 'orange', legend = '10-year roling window')
    psigma.title.text_font_size = '11pt'
    psigma.legend.location = 'top_right'
    psigma.legend.background_fill_alpha = 0.5
    plot = column(pmu, psigma)
    show(plot)

In [429]:
# Calculate VaR and ES using parametric method

def parametric(v0, mu, sigma, VaR_prob, ES_prob, t):
    VaR = v0 - v0 * np.exp(sigma * np.sqrt(t) * stat.norm.ppf(1-VaR_prob) + (mu - np.square(sigma)/2) * t)
    ES = v0 * (1 - np.array(stat.norm.cdf(stat.norm.ppf(1-ES_prob) - np.sqrt(t)*sigma)) * np.array(np.exp(mu*t)/(1-ES_prob)))
    return VaR, ES

In [430]:

# Calculate VaR and ES using historical method

def historical(v0, price, VaR_prob, ES_prob, window_days, horizon_days):
    npaths = window_days - horizon_days
    ntrials = len(price) - window_days
    price_log = np.log(price)
    return_xdays = np.array(price_log[:(len(price_log)-horizon_days)]) - np.array(price_log[5:])
    price_res = v0 * np.exp(return_xdays)
    scenarios = np.zeros(shape=(npaths,ntrials))
    for i in range(ntrials):
        scenarios[0:npaths,i] = price_res[i:i+npaths]
    scenarios_sorted = np.sort(scenarios, axis=0)
    VaR = v0 - scenarios_sorted[np.ceil((1-VaR_prob)*npaths).astype(int) - 1]
    ES = v0 - np.mean(scenarios_sorted[0:(np.ceil((1-ES_prob)*npaths).astype(int))], axis=0)
    return VaR, ES

In [431]:
# Calculate VaR and ES using Monte Carlo method

def monte_carlo(v0, price, mu, sigma, VaR_prob, ES_prob, window_days, horizon):
    npaths = 5000
    ntrials = len(price) - window_days
    p1 = np.zeros(shape=(npaths,ntrials))
    for i in range(ntrials):
        tv = np.ones(shape =(npaths,1))*horizon
        bm = np.sqrt(horizon) * np.random.randn(npaths,1)
        y = v0 * np.exp(sigma[i] * bm - (mu[i] + sigma[i]*sigma[i]/2) * tv)
        p1[:,i] = y[:,0]
    p2 = np.sort(p1,axis = 0)
    VaR = v0 - p2[np.ceil((1-VaR_prob)*npaths).astype(int) - 1]
    ES = v0 - np.mean(p2[0:(np.ceil((1-ES_prob)*npaths).astype(int))], axis=0)
    return VaR, ES

In [432]:
# VaR/ES plot

def plot_risk(v0, price, VaR_prob, ES_prob, method, window, horizon, plot_length):
    if method == 'Parametric Method':
        rtn, mu, sigma, mubar, sigmabar = gbm_est(price, window*252)
        VaR, ES = parametric(v0, mu, sigma, VaR_prob, ES_prob, horizon)
    elif method == 'Historical Method':
        VaR, ES = historical(v0, price, VaR_prob, ES_prob, int(window*252), int(horizon*252))
    elif method == 'Monte Carlo':
        rtn, mu, sigma, mubar, sigmabar = gbm_est(price, window*252)
        VaR, ES = monte_carlo(v0, price, mu, sigma, VaR_prob, ES_prob, window*252, horizon)
    else:
        sys.exit('Error!')
        
    length = min(len(VaR), len(ES), plot_length)
    VaR_ES = pd.DataFrame({'VaR': VaR[:length], 'ES': ES[:length]}, index = price.index[:plot_length])
    plot = figure(width=600, height=400, title = "VaR/ES", x_axis_type="datetime")
    plot.line(VaR_ES.index, VaR_ES['VaR'], color = 'green', legend = 'VaR')
    plot.line(VaR_ES.index, VaR_ES['ES'], color = 'blue', legend = 'ES')
    plot.legend.location = 'bottom_left'
    plot.title.text_font_size = '11pt'
    
    share_change = np.divide(price[:(len(price)-int(horizon*252))], price[int(horizon*252):])
    loss = v0 - share_change * v0
    length_loss = min(len(loss), len(VaR), plot_length)
    test = pd.DataFrame({'VaR': VaR[int(horizon*252):length_loss], 'Loss': loss[:(length_loss-int(horizon*252))]},
                   index = price.index[int(horizon*252):length_loss])  
    plot_test = figure(width=600, height=400, title = "VaR/ActualLoss", x_axis_type="datetime")
    plot_test.line(test.index, test['VaR'], color = 'green', legend = 'VaR')
    plot_test.line(test.index, test['Loss'], color = 'blue', legend = 'Actual Loss')
    plot_test.legend.location = 'bottom_left'
    plot_test.title.text_font_size = '11pt'
    output_notebook()  
    show(column(plot,plot_test))

In [433]:
# Black Scholes method to calculate put option price

def bs_put(stock, rf, sigma, strike, maturity):
    sigrt = 1/(sigma*np.sqrt(maturity))
    sig2 = sigma*sigma/2
    lsk = np.log(stock/strike)
    ert = np.exp(-rf*maturity)
    d1 = sigrt*(lsk+(rf+sig2)*maturity)
    d2 = sigrt*(lsk+(rf-sig2)*maturity)
    pr = stat.norm.cdf(-d2)*strike*ert-stat.norm.cdf(-d1)*stock
    return pr

In [434]:

# MC method to calculate option portfolio VaR
# Compute MC VaR for portfolio of a stock and a put option. % the stocks, assuming option implied vols are unchanged.

def option_mc(s0, mu, sigma, rf, iv, strike, mat, nstocks, nputs, VaR_prob, horizon):
    npaths = 1000000
    tv = np.ones(shape =(npaths,1))*horizon
    bm = np.sqrt(horizon) * np.random.randn(npaths,1)
    st = s0 * np.exp(sigma * bm - (mu + sigma*sigma/2) * tv)
    vtStock = st * nstocks
    v0Stock = s0 * nstocks
    putt = bs_put(st, rf, iv, strike, mat-horizon)
    vtPut = nputs * putt
    put0 = bs_put(s0, rf, iv, strike, mat)
    v0Put = nputs * put0
    loss = v0Stock + v0Put - (vtStock + vtPut)
    VaR = np.percentile(loss, 100*VaR_prob)
    return VaR

In [435]:
# Option portfolio calculations

def options_cal(options, rf, mat, imp_vol, v0, liq_rate, VaR_prob, window, horizon):
    rtn, mu, sigma, mubar, sigmabar = gbm_est(options, window*252)
    mu = mu[0]
    sigma = sigma[0]
    VaR_1, ES_1 = parametric(v0, mu, sigma, VaR_prob, 0.975, horizon)
    s0 = options[0]
    strike = options[0]
    nstocks = v0 * (1-liq_rate) / s0
    put0 = bs_put(s0, rf, imp_vol, strike, mat)
    nputs = v0 * liq_rate / put0
    VaR_2 = option_mc(s0, mu, sigma, rf, imp_vol, strike, mat, nstocks, nputs, VaR_prob, horizon)
    reduction = 100*(1-VaR_2/VaR_1)
    return s0, nstocks, put0, nputs, VaR_1, VaR_2, reduction


In [436]:
## PART 1: STOCK ANALYSIS ##

In [437]:
### Set up input

position_date_1 = datetime.datetime(1992, 2, 5)   # first day of plot
end_date_1 = datetime.datetime(2018, 12, 14)        # pick up a date for testing, may remove later and set today as default
ticker_1 = "BAC"                                  # Stock ticker (string)

### VaR/ES input
v0_1 = 10000                                         # initial investment
VaR_prob_1 = 0.99
ES_prob_1 = 0.975
window_1 = 5                                         # using 5 years historical data for estimation
horizon_days_1 = 5                                   # 5 days VaR/ES
method_1 = 'Parametric Method'

# Not input, prepared for further analysis
window_days_1 = window_1 * 252                         # convert to days
horizon_1 = horizon_days_1/252                         # convert to years
start_date_1 = position_date_1 - dateutil.relativedelta.relativedelta(years = 5)      # fetch data starting from start_date
price_1 = web.DataReader(ticker_1, 'yahoo', start_date_1, end_date_1)['Adj Close'].sort_index(ascending = False)  
plot_length_1 = len(price_1[price_1.index >= position_date_1])

In [438]:
def plot_price_stock():
    plot_price(price_1, plot_length_1)

def plot_parameters_stock():
    plot_parameters(price_1)
    
def plot_risk_stock():
    plot_risk(v0_1, price_1, VaR_prob_1, ES_prob_1, method_1, window_1, horizon_1, plot_length_1)
    


In [439]:
## PART 2: PORTFOLIO ANALYSIS ##

In [440]:
### Set up input

position_date = datetime.datetime(1992, 2, 5)   # first day of plot
end_date = datetime.datetime(2018, 12, 14)        # pick up a date for testing, may remove later and set today as default
tickers_string = "AAPL,BAC,GE,M"   # a string; as an example, tickers separated by comma.
weight_string = "0.25,0.25,0.25,0.25"
    
### VaR/ES input
v0 = 10000                                         # initial investment
VaR_prob = 0.99
ES_prob = 0.975
window = 5                                         # using 5 years historical data for estimation
horizon_days = 5                                   # 5 days VaR/ES
method = 'Parametric Method'

# Not input, prepared for further analysis
#weight_list = map(float, weight_string.split(",")) 
weight_list = np.array(weight_string.split(",")).astype(np.float)
    # split the string by the commas, and map each string in the resulting list into a float
tickers_list = tickers_string.split(",")  # split the string by the commas into a list of strings

window_days = window * 252                         # convert to days
horizon = horizon_days/252                         # convert to years
start_date = position_date - dateutil.relativedelta.relativedelta(years = 5)      # fetch data starting from start_date 
d={}
for ticker in tickers_list:
    d["{0}".format(ticker)] = web.DataReader(ticker, 'yahoo', start_date, end_date)['Adj Close'].rename(ticker)
df = pd.DataFrame(d).sort_index(ascending = False)  
plot_length = len(df[df.index >= position_date])

# Compute portfolio price
shares = np.round(np.divide(v0 * weight_list, np.array(df.ix[position_date])))
portfolio = pd.DataFrame({'Price': np.matmul(df, shares)}, index = df.index)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:32: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated



In [441]:
def plot_price_portfolio():
    plot_price(portfolio['Price'], plot_length)
    
def plot_parameters_portfolio():
    plot_parameters(portfolio['Price'])

def plot_risk_portfolio():
    plot_risk(v0, portfolio['Price'] , VaR_prob, ES_prob, method, window, horizon, plot_length)


In [442]:
## Option VaR ##

In [443]:

# Set up input

position_date_opt = datetime.datetime(2016, 12, 21)       # on which day to calculate VaR
ticker_opt = "AAPL"                                       # Stock ticker (string)

window_opt = 5
horizon_days_opt = 5
rf = 0.005            # risk free interest rate
VaR_prob_opt = 0.99
mat = 6/12            # options maturity in year
imp_vol = 0.21        # implied vol
v0_opt = 10000        # initial investment
liq_rate = 0.01       # iquidate 1% of portfolio and buy put options.

# not input, prepared for further calculation
start_date_opt = position_date_opt - dateutil.relativedelta.relativedelta(years = 2) 
options = web.DataReader(ticker_opt, 'yahoo', start_date_opt, position_date_opt)['Adj Close'].sort_index(ascending = False)  
horizon_opt = horizon_days_opt / 252

In [444]:
def option_portfolio_analysis():
    s0, nstocks, put0, nputs, VaR_1, VaR_2, reduction = options_cal(options, rf, mat, imp_vol, v0_opt, liq_rate, VaR_prob_opt, window_opt, horizon_opt)
    print ("Stock price:", s0)
    print ("Stock shares:", nstocks)
    print ("Put price on one share:", put0)
    print ("Put shares:", nputs)
    print ("VaR without options:", VaR_1)
    print ("VaR with options:", VaR_2)
    print ("VaR reduction (%):", reduction)

In [445]:
plot_price_stock()

Loading BokehJS ...

In [446]:
plot_parameters_stock()

Loading BokehJS ...

In [447]:
plot_risk_stock()

Loading BokehJS ...

In [448]:
plot_price_portfolio()

Loading BokehJS ...

In [449]:
plot_parameters_portfolio()

Loading BokehJS ...

In [450]:
plot_risk_portfolio()

/anaconda3/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:879: RuntimeWarning:

invalid value encountered in greater

/anaconda3/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:879: RuntimeWarning:

invalid value encountered in less

/anaconda3/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:1738: RuntimeWarning:

invalid value encountered in greater_equal



Loading BokehJS ...

In [451]:
option_portfolio_analysis()

Stock price: 112.7567138671875
Stock shares: 87.79964988746383
Put price on one share: 6.52540672793738
Put shares: 15.324715250601562
VaR without options: 505.24526434773907
VaR with options: 462.54326522764904
VaR reduction (%): 8.451736638287421


In [452]:
### Set up input

position_date = datetime.datetime(1992, 2, 5)   # first day of plot
end_date = datetime.datetime(2018, 12, 14)        # pick up a date for testing, may remove later and set today as default
tickers_string = "AAPL,BAC,GE,M"   # a string; as an example, tickers separated by comma.
weight_string = "0.25,0.25,0.25,0.25"
    
### VaR/ES input
v0 = 10000                                         # initial investment
VaR_prob = 0.99
ES_prob = 0.975
window = 5                                         # using 2 years historical data for estimation
horizon_days = 5                                   # 5 days VaR/ES
method = 'Historical Method'

# Not input, prepared for further analysis
#weight_list = map(float, weight_string.split(",")) 
weight_list = np.array(weight_string.split(",")).astype(np.float)
    # split the string by the commas, and map each string in the resulting list into a float
tickers_list = tickers_string.split(",")  # split the string by the commas into a list of strings

window_days = window * 252                         # convert to days
horizon = horizon_days/252                         # convert to years
start_date = position_date - dateutil.relativedelta.relativedelta(years = 5)      # fetch data starting from start_date 
d={}
for ticker in tickers_list:
    d["{0}".format(ticker)] = web.DataReader(ticker, 'yahoo', start_date, end_date)['Adj Close'].rename(ticker)
df = pd.DataFrame(d).sort_index(ascending = False)  
plot_length = len(df[df.index >= position_date])

# Compute portfolio price
shares = np.round(np.divide(v0 * weight_list, np.array(df.ix[position_date])))
portfolio = pd.DataFrame({'Price': np.matmul(df, shares)}, index = df.index)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:32: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated



In [453]:
plot_parameters_portfolio()

Loading BokehJS ...

In [454]:
plot_risk_portfolio()

Loading BokehJS ...

In [455]:
### Set up input

position_date = datetime.datetime(1992, 2, 5)   # first day of plot
end_date = datetime.datetime(2018, 12, 14)        # pick up a date for testing, may remove later and set today as default
tickers_string = "AAPL,BAC,GE,M"   # a string; as an example, tickers separated by comma.
weight_string = "0.25,0.25,0.25,0.25"
    
### VaR/ES input
v0 = 10000                                         # initial investment
VaR_prob = 0.99
ES_prob = 0.975
window = 5                                        # using 2 years historical data for estimation
horizon_days = 5                                   # 5 days VaR/ES
method = 'Monte Carlo'

# Not input, prepared for further analysis
#weight_list = map(float, weight_string.split(",")) 
weight_list = np.array(weight_string.split(",")).astype(np.float)
    # split the string by the commas, and map each string in the resulting list into a float
tickers_list = tickers_string.split(",")  # split the string by the commas into a list of strings

window_days = window * 252                         # convert to days
horizon = horizon_days/252                         # convert to years
start_date = position_date - dateutil.relativedelta.relativedelta(years = 5)      # fetch data starting from start_date 
d={}
for ticker in tickers_list:
    d["{0}".format(ticker)] = web.DataReader(ticker, 'yahoo', start_date, end_date)['Adj Close'].rename(ticker)
df = pd.DataFrame(d).sort_index(ascending = False)  
plot_length = len(df[df.index >= position_date])

# Compute portfolio price
shares = np.round(np.divide(v0 * weight_list, np.array(df.ix[position_date])))
portfolio = pd.DataFrame({'Price': np.matmul(df, shares)}, index = df.index)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:32: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated



In [456]:
plot_parameters_portfolio()

Loading BokehJS ...

In [457]:
plot_risk_portfolio()

Loading BokehJS ...